In [1]:
import pandas as pd
import geopandas as gpd
from pathlib import Path

In [2]:
DATA_PATH = Path.cwd().parent / 'data'

In [4]:
ttops_df = pd.read_csv(DATA_PATH / 'ttops.csv')

# Update 'Unnamed: 0' column to 'height'
ttops_df.rename(columns={'Unnamed: 0': 'HT'}, inplace=True)

# Update 'treeID' column to 'x' and strip 'c(' from the beginning
ttops_df['x'] = ttops_df['treeID'].str.strip('c(')

# Update 'Z' column to 'y'
ttops_df.rename(columns={'Z': 'y'}, inplace=True)

# Drop unnamed column, treeID, and geometry columns
ttops_df.drop(columns=['treeID', 'geometry'], inplace=True)

# Reset index
ttops_df.reset_index(drop=True, inplace=True)

# Load the dataframe into a geodataframe
ttops_gdf = gpd.GeoDataFrame(ttops_df, geometry=gpd.points_from_xy(ttops_df.x, ttops_df.y), crs='EPSG:5070')
ttops_gdf = ttops_gdf.to_crs('EPSG:4326')

# Update x and y columns to match the geometry
ttops_gdf["x"] = ttops_gdf["geometry"].x
ttops_gdf["y"] = ttops_gdf["geometry"].y
ttops_gdf.drop(columns=['geometry'], inplace=True)

# Convert the height column from meters to feet
ttops_gdf['HT'] = ttops_gdf['HT'] * 3.28084

# Drop heights greater than 160ft
ttops_gdf = ttops_gdf[ttops_gdf['HT'] <= 160]

# Save to a csv
ttops_gdf.to_csv(DATA_PATH / 'ttops_clean.csv', index=False)